<a href="https://colab.research.google.com/github/selgebali/Colabs/blob/main/RelatedIDs_perClientID.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Related Identifiers knowledge graphs per provider

Script to plot DOIs that have more than 3 related IDs from a specific provider using API queries.
## Network description:
* central node: a DOI with more than 3 relatedIDs
* Connections: type of relation
* Connected nodes: ResourceTypes with PIDs and with ResourceTypeGeneral annotated
## Related API Queries:
* Query for provider:
  * https://api.datacite.org/dois?client-id=ZBW.ZBW-JDA
  * https://api.datacite.org/dois?client-id=GESIS.GESIS

## Query parameters:

* **has-affiliation**
  * boolean
  * Return DOIs where either creators.affiliation.affiliationIdentifierScheme or contributors.affiliation.affiliationIdentifierScheme has at least one "ROR" value.

* **has-person**
  * boolean
  * Return DOIs where creators.nameIdentifiers.nameIdentifierScheme has at least one "ORCID" value.

* **has-organization**
  * boolean
  * Return DOIs where either creators.nameIdentifiers.nameIdentifierScheme or contributors.nameIdentifiers.nameIdentifierScheme has at least one "ROR" value.
* **has-funder**
  * boolean
  * Return DOIs where fundingReferences.funderIdentifierType has at least one "Crossref Funder ID" value.
* page[number]
  * integer
  * Page number for pagination.

* page[size]
  * integer
  * 0 to 1000
  * Page size between 0 and 1,000 for pagination.
-----
## FID providers to check & DataCite client ID:
* **ZBW Journal Data Archive (Economics): ZBW.ZBW-JDA**
  * DataCite  Members > Leibniz Institute for the Social Sciences > Consortium Organizations > German National Library of Economics > Repositories > ZBW Journal Data Archive
  * Leibniz has 81,929 DOIs
  * ZBW has 1,949 findable DOIs
  * https://commons.datacite.org/repositories/k6qcwl
  * RTGs: Collections

* **GESIS Data Archive (Social Science): GESIS.GESIS **
  * DataCite > Members  Leibniz Institute for the Social Sciences > Consortium Organizations >  Leibniz Institute for the Social Sciences >  Repositories: GESIS Data Archive
  * 9,679 findable DOIs
  * https://commons.datacite.org/repositories/y79cj1
  * 99% Datasets
  * Licenses unknown

## Code blocks (definitions):
* Custom color palette
* API queries:
  * Query for RelatedIDs more than 3
  * Query for RelationTypes
* Text formatt & wrapping
* Visualization of nodes and edges
* Main calling functions

## General links:
* https://support.datacite.org/reference/get_dois


## relatedIdentifierType
ARK,
arXiv,
bibcode,
CSTR,
DOI,
EAN13,
EISSN,
Handle,
IGSN,
ISBN,
ISSN,
ISTC,
LISSN,
LSID,
PMID,
PURL,
RRID
UPC,
URL,
URN,
w3id,
## relationType
IsCitedBy
Cites
IsSupplementTo
IsSupplementedBy
IsContinuedBy
Continues
Describes
IsDescribedBy
HasMetadata
IsMetadataFor
HasVersion
IsVersionOf
IsNewVersionOf
IsPreviousVersionOf
IsPartOf
HasPart
IsPublishedIn
IsReferencedBy
References
IsDocumentedBy
Documents
IsCompiledBy
Compiles
IsVariantFormOf
IsOriginalFormOf
IsIdenticalTo
IsReviewedBy
Reviews
IsDerivedFrom
IsSourceOf
IsRequiredBy
Requires
Obsoletes
IsObsoletedBy
IsCollectedBy
Collects
IsTranslationOf
HasTranslation
## resourceTypeGeneral
Audiovisual
Award
Book
BookChapter
Collection
ComputationalNotebook
ConferencePaper
ConferenceProceeding
DataPaper
Dataset
Dissertation
Event
Image
Instrument
InteractiveResource
Journal
JournalArticle
Model
OutputManagementPlan
PeerReview
PhysicalObject
Preprint
Project
Report
Service
Software
Sound
Standard
StudyRegistration
Text
Workflow
Other

In [ ]:
# Centralized configuration and constants
# Custom color palette
custom_colors = {
    'Instrument': '#243B54',
    'Creator': '#00B1E2',
    'Contributor': '#5B88B9',
    'Publisher': '#46BCAB',
    'RelatedItem': '#90D7CD'
}

# Defaults
DEFAULT_LIMIT = 50
DEFAULT_PAGE_SIZE = DEFAULT_LIMIT

# Output files
HTML_FILE = "merged_knowledge_graphs.html"
NODES_CSV = "merged_nodes.csv"
EDGES_CSV = "merged_edges.csv"

## fetch DOIs from GESIS.GESIS via the DataCite API,
	* keep only those with > 3 related identifiers,
	*	enrich related DOIs to retrieve their resourceTypeGeneral/resourceType, and
	*	plot a network where:
	*	central node = the DOI,
	*	connections = the relationType,
	*	connected nodes = the related PIDs (identifier + type), annotated with resourceTypeGeneral when resolvable.

In [97]:


# ============================================================
# VIZ CONFIG: edge/curve and layout tuning
# ============================================================

# Custom color palette, can be overridden in other blocks
custom_colors = {
    'Instrument': '#243B54',
    'Creator': '#00B1E2',
    'Contributor': '#5B88B9',
    'Publisher': '#46BCAB',
    'RelatedItem': '#F07C73'
}

RADIUS = 1.8          # circle radius for related nodes (controls edge length)
CURVATURE = 0.22      # base curvature for edges (0 = straight line)
CURVE_JITTER = 0.06   # small +/- added to curvature to reduce overlaps
EDGE_SAMPLES = 80     # points per edge curve
EDGE_WIDTH = 2
EDGE_COLOR = "#888"

# Core settings
CLIENT_ID = "GESIS.GESIS"
PAGE_SIZE = 1000                 # DataCite allows up to 1000
MAX_PAGES = 10                   # safety cap (adjust as needed)
TIMEOUT = 30                     # seconds for HTTP timeout
RETRY = 3                        # simple retry attempts
SLEEP_BETWEEN_CALLS = 0.2        # polite pacing for API calls

# Filtering
MIN_RELATED_IDS = 4              # "more than 3" => keep >= 4
MAX_RELATED_IDS = 10             # "up to 10"

# Output
HTML_FILE = "gesis_relatedids_graphs.html"
NODES_CSV = "gesis_nodes.csv"
EDGES_CSV = "gesis_edges.csv"

# Plot sizing
FIG_W = 1000
FIG_H = 1000

In [98]:
# ============================================================
# UTILS: text wrapping, safe requests, small helpers
# ============================================================

def wrap_text(text: str, width: int = 24) -> str:
    """Wrap long labels for nicer Plotly rendering."""
    return "<br>".join(textwrap.wrap(text, width=width))

def safe_get(url: str, timeout: int = TIMEOUT, retry: int = RETRY) -> requests.Response:
    """
    GET with simple retries and a short backoff.
    Raises the last exception if all retries fail.
    """
    last_err: Optional[Exception] = None
    for _ in range(retry):
        try:
            resp = requests.get(url, timeout=timeout)
            if 200 <= resp.status_code < 300:
                return resp
            last_err = RuntimeError(f"HTTP {resp.status_code}: {resp.text[:300]}")
        except Exception as e:
            last_err = e
        time.sleep(SLEEP_BETWEEN_CALLS)
    if last_err:
        raise last_err
    raise RuntimeError("safe_get failed unexpectedly without an error object")

def url_for_related_doi(doi: str) -> str:
    """
    DataCite endpoint for a single DOI resource.
    DOI must be URL-encoded (slashes included).
    """
    encoded = urllib.parse.quote(doi, safe="")
    return f"https://api.datacite.org/dois/{encoded}"

def normalize_string(s: Optional[str]) -> str:
    """None-safe strip."""
    return (s or "").strip()

In [99]:
# ============================================================
# API: fetch GESIS DOIs with *any* relatedIdentifiers (server-side prefilter)
# ============================================================
BASE_LIST_URL = "https://api.datacite.org/dois"

def build_list_url(client_id: str,
                   cursor: Optional[str] = None,
                   page_size: int = PAGE_SIZE) -> str:
    """
    Build a search URL that ensures at least one relatedIdentifier exists.
    Using cursor pagination; initial cursor '1' starts the stream.
    """
    params = {
        "client-id": client_id,
        "query": "relatedIdentifiers.relatedIdentifier:*",
        "page[size]": str(page_size),
        "disable-facets": "true"
        # Note: DataCite ignores unknown params. 'publisher=true' removed.
    }
    params["page[cursor]"] = "1" if cursor is None else cursor
    q = "&".join(f"{k}={urllib.parse.quote(v)}" for k, v in params.items())
    return f"{BASE_LIST_URL}?{q}"

def fetch_all_items_for_client(client_id: str,
                               max_pages: int = MAX_PAGES,
                               page_size: int = PAGE_SIZE) -> List[Dict[str, Any]]:
    """
    Pull paginated results for a client, prefiltered to have any relatedIdentifier.
    """
    items: List[Dict[str, Any]] = []
    cursor: Optional[str] = None

    for _ in range(max_pages):
        url = build_list_url(client_id, cursor, page_size)
        resp = safe_get(url)
        payload = resp.json()
        data = payload.get("data", [])
        items.extend(data)

        links = payload.get("links") or {}
        next_link = links.get("next")
        if not next_link:
            break

        # Extract next cursor from the "next" link's query (page[cursor]=...)
        parsed = urllib.parse.urlparse(next_link)
        q = urllib.parse.parse_qs(parsed.query)
        next_cursor = q.get("page[cursor]", [None])[0]
        if not next_cursor or next_cursor == cursor:
            break
        cursor = next_cursor

        time.sleep(SLEEP_BETWEEN_CALLS)

    return items

In [100]:
# ============================================================
# FILTERS: count & keep only records with >= MIN_RELATED_IDS
# ============================================================
def count_related_ids_from_api_item(item: Dict[str, Any]) -> int:
    """Count related IDs directly from a DataCite API item (raw JSON)."""
    attrs = item.get("attributes", {}) or {}
    rel = attrs.get("relatedIdentifiers") or []
    return len(rel)

def filter_api_items_by_related_ids(
    items: List[Dict[str, Any]],
    min_count: int = MIN_RELATED_IDS,
    max_count: int = MAX_RELATED_IDS
) -> List[Dict[str, Any]]:
    """
    Filter raw API items by number of related identifiers.
    Keeps only items with min_count ≤ related IDs ≤ max_count.
    Adds 'relatedIdCount' for convenience.
    """
    kept: List[Dict[str, Any]] = []
    for it in items:
        c = count_related_ids_from_api_item(it)
        if min_count <= c <= max_count:
            it_out = dict(it)
            it_out["relatedIdCount"] = c
            kept.append(it_out)
    return kept

In [101]:
# ============================================================
# ENRICH: resolve related DOIs to get resourceTypeGeneral/resourceType
# ============================================================
def resolve_related_target(related: Dict[str, Any]) -> Tuple[str, str, str]:
    """
    Given one 'relatedIdentifiers' item, return:
      (display_label, target_type_general, target_type_specific)

    - If relatedIdentifierType == 'DOI', fetch /dois/{doi} to read types.
    - Otherwise return 'Unknown' types but still display the PID.
    """
    identifier = normalize_string(related.get("relatedIdentifier"))
    # relation_type is used on edges; we keep it off the node label to reduce clutter
    identifier_type = normalize_string(related.get("relatedIdentifierType"))

    target_type_general = "Unknown"
    target_type_specific = "Unknown"

    if identifier and identifier_type.upper() == "DOI":
        try:
            r = safe_get(url_for_related_doi(identifier))
            obj = r.json().get("data", {}).get("attributes", {})
            types = obj.get("types", {}) or {}
            target_type_general = normalize_string(types.get("resourceTypeGeneral")) or "Unknown"
            target_type_specific = normalize_string(types.get("resourceType")) or "Unknown"
        except Exception:
            # Leave Unknown if not resolvable
            pass

    # Compact label for the related node: PID + (type hints)
    label_lines = [
        f"{identifier_type}:{identifier}" if identifier else "Unknown PID",
        f"RTG: {target_type_general}",
        f"RT: {target_type_specific}" if target_type_specific != "Unknown" else ""
    ]
    display_label = wrap_text("\n".join([l for l in label_lines if l]), width=24)
    return display_label, target_type_general, target_type_specific

In [102]:
# ============================================================
# VIZ HELPERS: radial layout and quadratic Bézier curves
# ============================================================

def radial_layout(G: nx.Graph, center_node: str, radius: float = RADIUS) -> Dict[str, Tuple[float, float]]:
    """Place center at (0,0) and others on a circle -> uniform edge lengths/clarity."""
    nodes = [n for n in G.nodes() if n != center_node]
    if not nodes:
        return {center_node: (0.0, 0.0)}
    angles = np.linspace(0, 2 * np.pi, len(nodes), endpoint=False)
    pos: Dict[str, Tuple[float, float]] = {center_node: (0.0, 0.0)}
    for n, theta in zip(nodes, angles):
        pos[n] = (radius * np.cos(theta), radius * np.sin(theta))
    return pos

def quad_bezier_curve(p0: Tuple[float, float],
                      p1: Tuple[float, float],
                      bend: float = CURVATURE,
                      samples: int = EDGE_SAMPLES) -> Tuple[np.ndarray, np.ndarray]:
    """
    Quadratic Bézier between p0 and p1.
    Control point is offset perpendicular to the segment by 'bend' * distance.
    """
    x0, y0 = p0
    x1, y1 = p1

    # Midpoint of the straight segment
    mx, my = (x0 + x1) / 2.0, (y0 + y1) / 2.0

    # Perpendicular unit vector to segment
    dx, dy = (x1 - x0), (y1 - y0)
    L = math.hypot(dx, dy) or 1.0
    perp_x, perp_y = -dy / L, dx / L  # rotate by 90°

    # Control point (offset out of the line)
    cx, cy = mx + bend * L * perp_x, my + bend * L * perp_y

    t = np.linspace(0, 1, samples)
    x_vals = (1 - t) ** 2 * x0 + 2 * (1 - t) * t * cx + t ** 2 * x1
    y_vals = (1 - t) ** 2 * y0 + 2 * (1 - t) * t * cy + t ** 2 * y1
    return x_vals, y_vals


In [106]:
# ============================================================
# VIZ: build a per-DOI knowledge graph (central + related items)
# ============================================================
def visualize_item(item: Dict[str, Any],
                   html_file: str = HTML_FILE,
                   nodes_csv: str = NODES_CSV,
                   edges_csv: str = EDGES_CSV) -> None:
    """
    Render one DOI as a star/radial graph:
      - central node = DOI
      - ring nodes   = related identifiers (optionally enriched by resolving DOIs)
    """
    # --- Extract basics
    attrs = item.get("attributes", {}) or {}
    doi = normalize_string(attrs.get("doi")) or "Unknown DOI"
    rels = attrs.get("relatedIdentifiers") or []

    # IMPORTANT FIX:
    # Do NOT shadow the imported module name `nx` inside this function.
    # (Previously, local variables named `nx, ny` for normals caused UnboundLocalError
    #  because Python treated `nx` as a local throughout the function, breaking nx.Graph().)
    G: nx.Graph = nx.Graph()

    # --- Node sizes
    node_size_map = {
        'Central': 320,
        'RelatedItem': 200
    }

    # --- Central node
    central_info = f"DOI: {doi}\nRelatedIDs: {len(rels)}"
    central_label = wrap_text(central_info, width=24)
    G.add_node(
        central_label,
        label='Central',
        size=node_size_map['Central'],
        color=custom_colors.get('Instrument', '#7f7f7f')  # central color
    )

    # --- Related nodes + edges
    for related in rels:
        display_label, target_type_general, _ = resolve_related_target(related)

        G.add_node(
            display_label,
            label='RelatedItem',
            size=node_size_map['RelatedItem'],
            color=custom_colors.get('RelatedItem', '#F07C73')
        )

        # store relationType for edge hover
        relation_type = normalize_string(related.get("relationType"))
        identifier_type = normalize_string(related.get("relatedIdentifierType"))

        G.add_edge(
            central_label,
            display_label,
            relationType=relation_type,
            identifierType=identifier_type,
            targetTypeGeneral=target_type_general
        )

        # We only sleep if we actually resolved a DOI (heuristic: identifierType == DOI)
        if identifier_type.upper() == "DOI":
            time.sleep(SLEEP_BETWEEN_CALLS)

    # --- Edge weights (minor layout hint)
    for u, v in G.edges():
        G.edges[u, v]['weight'] = 0.1

    # ------------------------------------------------------------
    # LAYOUT: radial for clarity (uniform edge lengths)
    # ------------------------------------------------------------
    pos = radial_layout(G, central_label, radius=RADIUS)

    # ------------------------------------------------------------
    # NODES
    # ------------------------------------------------------------
    node_x = [pos[n][0] for n in G.nodes()]
    node_y = [pos[n][1] for n in G.nodes()]
    node_size = [G.nodes[n]['size'] for n in G.nodes()]
    node_color = [G.nodes[n]['color'] for n in G.nodes()]
    node_text  = [n for n in G.nodes()]

    node_trace = go.Scatter(
        x=node_x, y=node_y,
        mode='markers+text',
        text=node_text,
        hovertext=node_text,
        hoverinfo='text',
        marker=dict(
            showscale=False,
            color=node_color,
            size=node_size,
            line_width=2,
            opacity=1.0
        ),
        textposition='middle center',
        textfont=dict(size=12, family='Arial', color='white')
    )

    # ============================================================
    # EDGES: curves + *annotation* labels centered & rotated
    # ============================================================
    edge_traces = []
    annotations = []

    sign = 1
    for (a, b) in G.edges():
        p0, p1 = pos[a], pos[b]
        # Alternate bend sign to reduce overlaps, with a little jitter
        bend = sign * (CURVATURE + (CURVE_JITTER if sign > 0 else -CURVATURE))
        sign *= -1

        # Quadratic Bézier points
        x_vals, y_vals = quad_bezier_curve(p0, p1, bend=bend, samples=EDGE_SAMPLES)

        # Hover text
        rel = G.edges[a, b].get("relationType", "")
        idt = G.edges[a, b].get("identifierType", "")
        ttg = G.edges[a, b].get("targetTypeGeneral", "")
        hover = f"relationType: {rel}<br>identifierType: {idt}<br>target RTG: {ttg}"

        # Edge line
        edge_traces.append(go.Scatter(
            x=x_vals, y=y_vals, mode='lines',
            line=dict(width=EDGE_WIDTH, color=EDGE_COLOR),
            hoverinfo='text',
            # Provide one hover text value per point to avoid warnings
            text=[hover] * len(x_vals)
        ))

        # ---- Label at curve midpoint, offset normal to curve, rotated along tangent
        mid_i = len(x_vals) // 2

        # Tangent via centered finite difference
        dx = x_vals[min(mid_i + 1, len(x_vals) - 1)] - x_vals[max(mid_i - 1, 0)]
        dy = y_vals[min(mid_i + 1, len(y_vals) - 1)] - y_vals[max(mid_i - 1, 0)]

        # angle in degrees for rotation
        angle = math.degrees(math.atan2(dy, dx))

        # unit normal for outward offset
        L = math.hypot(dx, dy) or 1.0
        n_perp_x, n_perp_y = -dy / L, dx / L  # NOTE: names avoid 'nx' shadowing!

        # configurable label offset
        LABEL_OFFSET = 0.08
        x_lab = x_vals[mid_i] + LABEL_OFFSET * n_perp_x
        y_lab = y_vals[mid_i] + LABEL_OFFSET * n_perp_y

        if rel:
            annotations.append(dict(
                x=x_lab, y=y_lab, xref='x', yref='y',
                text=rel,
                showarrow=False, align='center',
                textangle=angle,  # align label to edge direction
                font=dict(size=12, family='Arial', color='#111'),
                bgcolor='rgba(255,255,255,0.9)',
                bordercolor='rgba(0,0,0,0.2)',
                borderwidth=1, borderpad=2,
                opacity=1,
                captureevents=False
                # 'layer' isn't supported for annotations in Plotly → omit
            ))

    # ------------------------------------------------------------
    # FIGURE
    # ------------------------------------------------------------
    fig = go.Figure(
        data=edge_traces + [node_trace],
        layout=go.Layout(
            title=dict(text=f"Related Identifiers Graph — {doi}", x=0.5),
            showlegend=False, hovermode='closest',
            margin=dict(b=20, l=20, r=20, t=50),
            xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
            yaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
            width=FIG_W, height=FIG_H,
            plot_bgcolor='rgba(0,0,0,0)', paper_bgcolor='rgba(0,0,0,0)',
            annotations=annotations
        )
    )

    # ------------------------------------------------------------
    # OUTPUT: show and append to HTML; save node/edge rows
    # ------------------------------------------------------------
    fig.show()

    # Append (don't rewrite) the HTML so multiple figures are collected
    with open(html_file, "a", encoding="utf-8") as f:
        f.write(pio.to_html(fig, include_plotlyjs="cdn"))

    node_rows = [
        {"Node": n,
         "Label": G.nodes[n]['label'],
         "Color": G.nodes[n]['color'],
         "Size": G.nodes[n]['size']}
        for n in G.nodes()
    ]
    edge_rows = [
        {"Source": s,
         "Target": t,
         "relationType": G.edges[s, t].get("relationType", ""),
         "identifierType": G.edges[s, t].get("identifierType", ""),
         "targetTypeGeneral": G.edges[s, t].get("targetTypeGeneral", "")}
        for (s, t) in G.edges()
    ]

    # Append to CSVs; write headers only once if files don't exist yet
    pd.DataFrame(node_rows).to_csv(
        nodes_csv, mode='a', index=False,
        header=not os.path.exists(nodes_csv), encoding='utf-8'
    )
    pd.DataFrame(edge_rows).to_csv(
        edges_csv, mode='a', index=False,
        header=not os.path.exists(edges_csv), encoding='utf-8'
    )

In [107]:
# ============================================================
# SORTING: prioritize DOIs with the most related identifiers
# ============================================================
def sort_items_by_related_count(items: List[Dict[str, Any]]) -> List[Dict[str, Any]]:
    """Sort API items in descending order by number of relatedIdentifiers."""
    def related_count(it: Dict[str, Any]) -> int:
        return len((it.get("attributes", {}) or {}).get("relatedIdentifiers") or [])
    return sorted(items, key=related_count, reverse=True)

In [108]:
# ============================================================
# MAIN: orchestrate fetch → filter → visualize
# ============================================================
def init_html(path: str) -> None:
    """Create/overwrite the HTML container file."""
    with open(path, "w", encoding="utf-8") as f:
        f.write("<html><head><title>GESIS Related Identifiers Knowledge Graphs</title></head><body>")

def close_html(path: str) -> None:
    """Close the container HTML file."""
    with open(path, "a", encoding="utf-8") as f:
        f.write("</body></html>")

def main() -> None:
    print("Fetching items for client:", CLIENT_ID)
    init_html(HTML_FILE)

    items = fetch_all_items_for_client(CLIENT_ID, max_pages=MAX_PAGES, page_size=PAGE_SIZE)
    print(f"Fetched {len(items)} items (pre-filter).")

    # Apply both min and max thresholds
    filtered = filter_api_items_by_related_ids(
        items,
        min_count=MIN_RELATED_IDS,
        max_count=MAX_RELATED_IDS
    )
    print(f"Kept {len(filtered)} items with between {MIN_RELATED_IDS} and {MAX_RELATED_IDS} related identifiers.")

    # Sort by number of related IDs (descending)
    filtered = sort_items_by_related_count(filtered)
    print("Sorted DOIs by number of related identifiers (highest → lowest).")

    # Optional: quick summary (top 10)
    print("\nTop 10 DOIs by number of related identifiers:")
    for idx, it in enumerate(filtered[:10], start=1):
        attrs = it.get("attributes", {}) or {}
        doi = attrs.get("doi", "Unknown DOI")
        rel_count = len(attrs.get("relatedIdentifiers") or [])
        print(f"{idx:02d}. {doi} — {rel_count} related IDs")

    # Visualize all kept items
    for idx, it in enumerate(filtered, start=1):
        doi = (it.get("attributes", {}) or {}).get("doi", "Unknown DOI")
        print(f"[{idx}/{len(filtered)}] Visualizing {doi} ...")
        visualize_item(it, HTML_FILE, NODES_CSV, EDGES_CSV)

    close_html(HTML_FILE)
    print(f"Done.\nHTML: {HTML_FILE}\nNodes CSV: {NODES_CSV}\nEdges CSV: {EDGES_CSV}")

if __name__ == "__main__":
    main()

Fetching items for client: GESIS.GESIS
Fetched 1599 items (pre-filter).
Kept 141 items with between 4 and 10 related identifiers.
Sorted DOIs by number of related identifiers (highest → lowest).

Top 10 DOIs by number of related identifiers:
01. 10.4232/1.12742 — 10 related IDs
02. 10.4232/1.12743 — 10 related IDs
03. 10.4232/1.14186 — 10 related IDs
04. 10.4232/1.14527 — 10 related IDs
05. 10.4232/10.fisuzida2015.2 — 9 related IDs
06. 10.4232/1.12717 — 9 related IDs
07. 10.4232/1.12716 — 9 related IDs
08. 10.4232/1.14118 — 9 related IDs
09. 10.4232/1.14494 — 9 related IDs
10. 10.4232/1.12708 — 8 related IDs
[1/141] Visualizing 10.4232/1.12742 ...


[2/141] Visualizing 10.4232/1.12743 ...


[3/141] Visualizing 10.4232/1.14186 ...


[4/141] Visualizing 10.4232/1.14527 ...


[5/141] Visualizing 10.4232/10.fisuzida2015.2 ...


...

[50/141] Visualizing 10.4232/cils4eu-de.6656.7.0.0 ...


[51/141] Visualizing 10.4232/1.14290 ...


[52/141] Visualizing 10.4232/pairfam.5678.14.2.0 ...


[53/141] Visualizing 10.4232/1.14377 ...


KeyboardInterrupt: 